In [32]:
import pandas as pd
import folium
import requests
import json

In [33]:
# Data is updated daily by the Colordo Department of Public Health & Environment.
# Available via their API link on their website:
# https://data-cdphe.opendata.arcgis.com/datasets/colorado-covid-19-positive-cases-and-rates-of-infection-by-county-of-identification
url = 'https://opendata.arcgis.com/datasets/fbae539746324ca69ff34f086286845b_0.geojson'
co_data = requests.get(url)

In [34]:
co_json = json.loads(co_data.content)

In [35]:
for idx, val in enumerate(co_json['features']):
    if co_json['features'][idx]['properties']['County_Rate_Per_100_000'] == -1.0:
        co_json['features'][idx]['properties']['County_Rate_Per_100_000'] = 0
        
        
        

In [36]:
co_df = pd.json_normalize(co_json['features'])
co_df.head()

type  properties.OBJECTID properties.STAETFP properties.COUNTYFP  \
0  Feature                    1                 08                 109   
1  Feature                    2                 08                 115   
2  Feature                    3                 08                 017   
3  Feature                    4                 08                 027   
4  Feature                    5                 08                 067   

  properties.GEOID properties.COUNTY properties.LABEL properties.FULL_  \
0            08109          SAGUACHE         Saguache  Saguache County   
1            08115          SEDGWICK         Sedgwick  Sedgwick County   
2            08017          CHEYENNE         Cheyenne  Cheyenne County   
3            08027            CUSTER           Custer    Custer County   
4            08067          LA PLATA         La Plata  La Plata County   

   properties.County_Pos_Cases  properties.County_Population  ...  \
0                            3                          6837  ...   
1                            0                          2275  ...   
2                            0                          1862  ...   
3                            2                          4928  ...   
4                           44                         56403  ...   

   properties.State_Number_Tested  properties.State_Number_Hospitalizations  \
0                           37153                                      1417   
1                           37153                                      1417   
2                           37153                                      1417   
3                           37153                                      1417   
4                           37153                                      1417   

   properties.State_Deaths  properties.State_Number_of_Counties_Pos  \
0                      290                                       56   
1                      290                                       56   
2                      290                                       56   
3                      290                                       56   
4                      290                                       56   

  properties.State_Rate_Per_100000 properties.Shape__Area  \
0                           128.25           1.327387e+10   
1                           128.25           2.491282e+09   
2                           128.25           7.613551e+09   
3                           128.25           3.100362e+09   
4                           128.25           6.966608e+09   

   properties.Shape__Length  properties.State_Number_Outbreaks  geometry.type  \
0             529491.079019                                 68        Polygon   
1             208249.568714                                 68        Polygon   
2             373455.831824                                 68        Polygon   
3             290994.589030                                 68        Polygon   
4             371001.027724                                 68        Polygon   

                                geometry.coordinates  
0  [[[-106.871413337, 37.9419000440001], [-106.86...  
1  [[[-102.652123692, 40.8846387410001], [-102.65...  
2  [[[-102.576860462, 39.040682481], [-102.576966...  
3  [[[-105.79690713, 38.265053159], [-105.7967271...  
4  [[[-108.295174572, 37.215014852], [-108.295973...  

[5 rows x 26 columns]

In [38]:
co_df['properties.County_Rate_Per_100_000'] = co_df['properties.County_Rate_Per_100_000'].apply(lambda x: 0 if x == -1.0 else x)

In [44]:
m = folium.Map(location=(39, -104), zoom_start=6)

cp = folium.Choropleth(
    geo_data=co_json,
    name='choropleth',
    fill_color='YlOrRd',
    data=co_df,
    columns=['properties.COUNTY', 'properties.County_Rate_Per_100_000'],
    key_on='feature.properties.COUNTY',
    fill_opacity=0.7,
    line_opacity=0.2,
    legend_name='Infection Rate per 100,000',
    highlight=True
).add_to(m)

cp.geojson.add_child(
    folium.features.GeoJsonTooltip(['COUNTY', 'County_Population', 'County_Pos_Cases', 
                                   'County_Rate_Per_100_000']))
m

In [ ]:
m.save('CO_COVID_Rates.html')